In [33]:
""""0. initialize libraries and setup tools"""

%load_ext jupyternotify

import numpy as np
import gymnasium as gym
import math
import random
import matplotlib
import matplotlib.pyplot as plt
from collections import namedtuple, deque
from itertools import count
from tqdm import tqdm

import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torchvision import models
#from torchsummary import summary

env = gym.make('MountainCar-v0')

# set up matplotlib
is_ipython = 'inline' in matplotlib.get_backend()  # checks if one is running IPhyton environment like jupyter notebook
if is_ipython:
    from IPython import display

plt.ion()  # interactive mode on, allows automatic plots when data is updated (whithout calling plt.show every time)

# if GPU is to be used
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
   
    
    
    
""" 1.1. Helper functions """

def plot_durations(durations, hyperparameters):
    plt.figure()
    durations_t = torch.tensor(durations, dtype=torch.float)
    plt.title('Duration per Episode')
    plt.xlabel('Episode')
    plt.ylabel('Duration')
    plt.plot(durations_t.numpy())
    if len(durations_t) >= 100:
        means = durations_t[100:].unfold(0, 100, 1).mean(1).view(-1)
        plt.plot(range(100, len(durations)-99), means.numpy(), label='100 Moving Average')
    plt.savefig(f"DQN_Duration_Hyperparameters_{hyperparameters}.png", dpi=300)
    plt.close()
    
def plot_curve(data, title, xlabel, ylabel, savefig=False):
    plt.plot(data, label = 'title')
    plt.title(title)
    plt.xlabel(xlabel)
    plt.ylabel(ylabel)
    if savefig: 
        plt.savefig(f"{title}.png", dpi=300) # Use f-string to concatenate strings and variable
        
def plot_scatter(data, xlabel, ylabel):
    data_t = torch.tensor(data, dtype=torch.float)
    plt.title('Result')
    plt.xlabel(xlabel)
    plt.ylabel(ylabel)
    plt.scatter(list(range(len(data))), data_t.numpy()) # usually for plt.scatter you need (x,y) as arguments

def plot_with_average(data, xlabel, ylabel):
    plt.figure(1)
    data_t = torch.tensor(data, dtype=torch.float)
    plt.title('Result')
    plt.xlabel(xlabel)
    plt.ylabel(ylabel)
    plt.plot(list(range(len(data))), data_t.numpy(), label='Cumulative Reward Per Episode') 
    # Take 100 episode averages and plot them too
    if len(data_t) > 100:  # Check if data has more than 100 episodes
        # Calculate moving average starting from episode 100
        means = data_t[100:].unfold(0, 100, 1).mean(1).view(-1)
        # Plot the average line starting from episode 100
        plt.plot(range(100, len(data)-99), means.numpy(), label='Moving Average (100 episodes)')

def cumulative_sum(input_list):
    result = []
    running_total = 0
    for element in input_list:
        running_total += element
        result.append(running_total)
    return result



    
""""1.2. Define ReplayBuffer and deep q network"""

Transition = namedtuple('Transition',
                        ('state', 'action', 'next_state', 'reward', 'reward_int'))

class ReplayBuffer(object):

    def __init__(self, capacity):
        self.buffer = deque([], maxlen=capacity)

    def push(self, *args):
        self.buffer.append(Transition(*args)) #Save a transition

    def sample(self, batch_size):
        return random.sample(self.buffer, batch_size)

    def __len__(self):
        return len(self.buffer)

class DQN(nn.Module):

    def __init__(self, n_observations, n_actions, n_nodes_per_layer=64, n_layers=2):
        super(DQN, self).__init__()
        self.layers = nn.ModuleList([nn.Linear(n_observations, n_nodes_per_layer)])
        for _ in range(n_layers - 1):
            self.layers.append(nn.Linear(n_nodes_per_layer, n_nodes_per_layer))
        self.output_layer = nn.Linear(n_nodes_per_layer, n_actions)

    def forward(self, x):
        for layer in self.layers:
            x = F.relu(layer(x))
        return self.output_layer(x)
    
class RNDNetwork(nn.Module):
    def __init__(self, input_dim, output_dim):
        super(RNDNetwork, self).__init__()
        self.network = nn.Sequential(
            nn.Linear(input_dim, 128),
            nn.ReLU(),
            nn.Linear(128, 128),
            nn.ReLU(),
            nn.Linear(128, output_dim)
        )

    def forward(self, x):
        return self.network(x)
            
        
    

"""" 2. Agent class """

class DQNAgent:
    def __init__(self, BATCH_SIZE, GAMMA, EPS_START, EPS_END, EPS_DECAY, TAU, LR, n_actions, n_observations):
        self.BATCH_SIZE = BATCH_SIZE
        self.GAMMA = GAMMA
        self.EPS_START = EPS_START
        self.EPS_END = EPS_END
        self.EPS_DECAY = EPS_DECAY
        self.TAU = TAU
        self.LR = LR
        self.n_actions = n_actions
        self.n_observations = n_observations
        self.memory = ReplayBuffer(10000)
        self.policy_net = DQN(n_observations, n_actions).to(device)
        self.target_net = DQN(n_observations, n_actions).to(device)
        self.optimizer = optim.Adam(self.policy_net.parameters(), lr=LR)
        self.steps_done = 0
        self.episode_durations = []
        self.loss_per_episode = []
        self.cumulative_reward_per_episode = []
        self.cumulative_environment_reward_per_episode = []
        self.cumulative_auxiliary_reward_per_episode = []
        self.agent_performance = []

        self.reward_factor = 0.2
        self.target_net.load_state_dict(self.policy_net.state_dict())
        self.target_net.eval()
        
        self.predictor_net = RNDNetwork(n_observations, 1).to(device)
        self.target_rnd_net = RNDNetwork(n_observations, 1).to(device)
        for param in self.target_rnd_net.parameters():
            param.requires_grad = False  # Freeze target network

        # Initialize optimizer for predictor network
        self.rnd_optimizer = torch.optim.Adam(self.predictor_net.parameters(), lr=1e-4)

        # Running statistics for normalization
        self.states = []
        self.intrinsic_rewards = []
        self.rnd_mean = 0
        self.rnd_std = 1
        self.state_mean = torch.zeros(n_observations).to(device)
        self.state_std = torch.ones(n_observations).to(device)


    def select_action(self, state):
        sample = random.random()
        eps_threshold = self.EPS_END + (self.EPS_START - self.EPS_END) * math.exp(-1. * self.steps_done / self.EPS_DECAY)
        self.steps_done += 1
        if sample > eps_threshold:
            with torch.no_grad():
                return self.policy_net(state).max(1)[1].view(1, 1)
        else:
            return torch.tensor([[random.randrange(self.n_actions)]], device=device, dtype=torch.long)

    def optimize_model(self):
        if len(self.memory) < self.BATCH_SIZE:
            return
        transitions = self.memory.sample(self.BATCH_SIZE)
        batch = Transition(*zip(*transitions))
        
        non_final_mask = torch.tensor(tuple(map(lambda s: s is not None,
                                                batch.next_state)), device=device, dtype=torch.bool)
        non_final_next_states = torch.cat([s for s in batch.next_state
                                           if s is not None])
        state_batch = torch.cat(batch.state)
        action_batch = torch.cat(batch.action)
        reward_batch = torch.cat(batch.reward)
        reward_int_batch = torch.cat(batch.reward_int)
        
        state_action_values = self.policy_net(state_batch).gather(1, action_batch)
        
        next_state_values = torch.zeros(self.BATCH_SIZE, device=device)
        with torch.no_grad():
            next_state_values[non_final_mask] = self.target_net(non_final_next_states).max(1).values
        
        expected_state_action_values = (next_state_values * self.GAMMA) + reward_batch + reward_int_batch * self.reward_factor
        expected_state_action_values = expected_state_action_values.float()

        loss = F.smooth_l1_loss(state_action_values, expected_state_action_values.unsqueeze(1))
        
        self.optimizer.zero_grad()
        loss.backward()
        for param in self.policy_net.parameters():
            param.grad.data.clamp_(-1, 1)
        self.optimizer.step()

        self.update_rnd(non_final_next_states)
        
        return loss.item()

    def update(self, num_episodes):
        for episode in tqdm(range(num_episodes), desc="Episodes"):
            state, info = env.reset()
            state = torch.tensor(state, dtype=torch.float32, device=device).unsqueeze(0)
            cumulative_reward_t = 0
            environment_reward_t = 0
            auxiliary_reward_t = 0
            running_loss = []
            for t in count():
                self.update_running_stats(state)
                action = self.select_action(state)
                observation, reward, terminated, truncated, _ = env.step(action.item())
                environment_reward_t += reward
                reward_int = torch.zeros(1, dtype=torch.float32, device=device)
                if t > 2:
                    reward_int = torch.tensor([self.compute_rnd_reward(torch.tensor(observation, dtype=torch.float32, device=device))])
                reward_total = reward + reward_int * self.reward_factor
                #print(reward_total)
                self.intrinsic_rewards.append(reward_int)
                cumulative_reward_t += reward
                reward = torch.tensor([reward], device=device)
                done = terminated or truncated
                
                if not done:
                    next_state = torch.tensor(observation, dtype=torch.float32, device=device).unsqueeze(0)
                    self.agent_performance.append(1)
                else:
                    next_state = None
                if truncated:
                    self.agent_performance.append(0)
                    
                self.memory.push(state, action, next_state, reward, reward_int)
                state = next_state
                
                loss_value = self.optimize_model()
                
                target_net_state_dict = self.target_net.state_dict()
                policy_net_state_dict = self.policy_net.state_dict()
                for key in policy_net_state_dict:
                    target_net_state_dict[key] = policy_net_state_dict[key]*self.TAU + target_net_state_dict[key]*(1-self.TAU)
                self.target_net.load_state_dict(target_net_state_dict)

                if done:
                    self.episode_durations.append(t + 1)
                    break
                    
                running_loss.append(loss_value)
            
            filtered_running_loss = [loss for loss in running_loss if loss is not None]
            if filtered_running_loss:
                self.loss_per_episode.append(np.mean(filtered_running_loss))

            self.cumulative_reward_per_episode.append(cumulative_reward_t)
            self.cumulative_environment_reward_per_episode.append(environment_reward_t)
            self.cumulative_auxiliary_reward_per_episode.append(auxiliary_reward_t)

    def normalize_state(self, state):
        normalized_state = (state - self.state_mean) / (self.state_std + 1e-5)
        return torch.tensor(normalized_state, dtype=torch.float32)

    def update_rnd(self, state):
        # Normalize state
        normalized_state = self.normalize_state(state)

        # Get predictor and target outputs
        predictor_output = self.predictor_net(normalized_state)
        with torch.no_grad():
            target_output = self.target_rnd_net(normalized_state)

        # Compute loss
        loss_rnd = nn.MSELoss()(predictor_output, target_output)
        print(loss_rnd.item())

        # Optimize the predictor network
        self.rnd_optimizer.zero_grad()
        loss_rnd.backward()
        self.rnd_optimizer.step()

        # Update running statistics for RND reward normalization
        #rnd_diff = (predictor_output - target_output).detach().cpu().numpy()
        intrinsic_rewards = torch.cat(self.intrinsic_rewards)
        self.rnd_mean = intrinsic_rewards.mean()
        self.rnd_std = intrinsic_rewards.std()

        return loss_rnd.item()

    def compute_rnd_reward(self, state):
        normalized_state = self.normalize_state(state)
        with torch.no_grad():
            predictor_output = self.predictor_net(normalized_state)
            target_output = self.target_rnd_net(normalized_state)
        rnd_reward = torch.mean((predictor_output - target_output) ** 2)
        normalized_rnd_reward = (rnd_reward - self.rnd_mean) / self.rnd_std
        return torch.abs(torch.clamp(normalized_rnd_reward, -5, 5))
    
    def update_running_stats(self, new_state):
        self.states.append(new_state)
        self.state_mean = torch.tensor(np.mean(self.states, axis=0), dtype=torch.float32, device=device)
        self.state_std = torch.tensor(np.std(self.states, axis=0) + 1e-5, dtype=torch.float32, device=device)
    

"""" 3. Run Model """

def train_agent_with_hyperparameters(BATCH_SIZE, GAMMA, EPS_START, EPS_END, EPS_DECAY, TAU, LR, num_episodes=3000):
    n_actions = env.action_space.n
    n_observations = env.observation_space.shape[0]
    agent = DQNAgent(BATCH_SIZE, GAMMA, EPS_START, EPS_END, EPS_DECAY, TAU, LR, n_actions, n_observations)
    agent.update(num_episodes)
    hyperparameters = f"BATCH_SIZE={BATCH_SIZE}_GAMMA={GAMMA}_EPS_START={EPS_START}_EPS_END={EPS_END}_EPS_DECAY={EPS_DECAY}_TAU={TAU}_LR={LR}"
    plot_durations(agent.episode_durations, hyperparameters)

def hyperparameter_tuning():
    BATCH_SIZE = 64
    GAMMA = 0.99
    EPS_START = 0.9
    EPS_END = 0.1
    EPS_DECAY = 100000
    TAU = 0.0005 
    LR = 1e-4

    train_agent_with_hyperparameters(BATCH_SIZE, GAMMA, EPS_START, EPS_END, EPS_DECAY, TAU, LR)

#     for BATCH_SIZE in [32, 64, 128]:
#         train_agent_with_hyperparameters(BATCH_SIZE, GAMMA, EPS_START, EPS_END, EPS_DECAY, TAU, LR)
#    for GAMMA in [0.95, 0.90]:
#        train_agent_with_hyperparameters(BATCH_SIZE, GAMMA, EPS_START, EPS_END, EPS_DECAY, TAU, LR)
#     for EPS_START in [1.0, 0.9, 0.8]:
#         train_agent_with_hyperparameters(BATCH_SIZE, GAMMA, EPS_START, EPS_END, EPS_DECAY, TAU, LR)
#     for EPS_END in [0.1, 0.05, 0.01]:
#         train_agent_with_hyperparameters(BATCH_SIZE, GAMMA, EPS_START, EPS_END, EPS_DECAY, TAU, LR)
#     for EPS_DECAY in [10000, 100000, 1000000]:
#         train_agent_with_hyperparameters(BATCH_SIZE, GAMMA, EPS_START, EPS_END, EPS_DECAY, TAU, LR)
#     for TAU in [0.00005, 0.0005, 0.005]:
#         train_agent_with_hyperparameters(BATCH_SIZE, GAMMA, EPS_START, EPS_END, EPS_DECAY, TAU, LR)
#     for LR in [0.001, 0.0005, 0.0001]:
#         train_agent_with_hyperparameters(BATCH_SIZE, GAMMA, EPS_START, EPS_END, EPS_DECAY, TAU, LR)




# Run the hyperparameter tuning
hyperparameter_tuning()

The jupyternotify extension is already loaded. To reload it, use:
  %reload_ext jupyternotify


Episodes:   0%|          | 0/3000 [00:00<?, ?it/s]

0.02622978575527668
0.023478413000702858
0.021076474338769913
0.01860729791224003
0.016376376152038574
0.013675007969141006
0.012648790143430233
0.011889876797795296
0.009212099947035313
0.008160131983458996
0.00835235882550478
0.006805264391005039
0.0061071948148310184
0.005135526414960623
0.0043858811259269714
0.00400514854118228
0.0035450090654194355
0.003189404960721731
0.0027083063032478094
0.0026322882622480392
0.0023315995931625366
0.002363142091780901
0.0029238450806587934
0.0035956064239144325
0.002842632820829749
0.0036333738826215267
0.0033034170046448708
0.00278808013536036
0.0025259482208639383
0.0019259697292000055
0.0018260134384036064
0.001089205383323133
0.0013433607527986169
0.0011856500059366226
0.0013616458745673299
0.0013075125170871615
0.001104978146031499
0.000964073755312711
0.0010207478189840913
0.0009596156305633485
0.0009641720098443329
0.000940373633056879
0.0010804029880091548
0.0008125124149955809
0.0008987628971226513
0.0007687614997848868
0.0007548123830

/var/folders/mg/44g5ch495hdc8x4_5mq3dsdm0000gn/T/ipykernel_14286/622562488.py:292: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  return torch.tensor(normalized_state, dtype=torch.float32)


0.0001861532509792596
0.0002255620202049613
0.0002036348159890622
0.00026796775637194514
0.00019211029575672
0.00027818355010822415
0.0001843748614192009
0.00017124156875070184
0.0002605062327347696
0.000249484641244635
0.00026409554993733764
0.00022689229808747768


...

3.625276008278888e-07
3.3482714911770017e-07
3.2660440751897113e-07
2.5075209464375803e-07
2.6687433773986413e-07
3.886868853442138e-07
3.8749351460865e-07
3.286335754637548e-07
5.368962661123078e-07
5.496016228789813e-07
3.031052528967848e-07
3.8936707369430223e-07
2.9367072329478106e-07
4.5638665824299096e-07
7.038921694402234e-07
3.661786251996091e-07
4.1760031876947323e-07
3.192985502664669e-07
5.389779857978283e-07
2.0645684628561867e-07
4.1194806499333936e-07
3.5694154121301835e-07
2.5821827875915915e-07
8.705276854925614e-07
4.173053582690045e-07
9.926076245392323e-07
4.80182222872827e-07
5.869971460015222e-07
5.743305564465118e-07
2.4325109393430466e-07
3.739645251243928e-07
5.433177534541755e-07
2.0140930701018078e-07
2.9041152060926834e-07
2.587577228041482e-07
1.5164108901899453e-07
3.7174646649873466e-07
3.439582201281155e-07
3.343570824654307e-07
1.9470519418973709e-07
3.9741433965900796e-07
2.3035767071633018e-07
3.113257776021783e-07
2.8329245083114074e-07
4.939541895510

Episodes:  22%|██▏       | 647/3000 [21:51:47<117:51:09, 180.31s/it]

5.995663059366052e-07
5.437070740299532e-07
8.26483528726385e-07
4.374849140731385e-07
6.073581744203693e-07
4.866622589361214e-07
3.0975695608503884e-07
4.2490731289035466e-07
5.139645509188995e-07
2.995089971591369e-07
3.0309502108138986e-07
3.4284110483895347e-07
3.114952562555118e-07
3.5320502433933143e-07
6.525358458020492e-07
3.173981042436935e-07
3.661259313503251e-07
2.368322213897045e-07
3.894710687291081e-07
2.9253089905978413e-07
2.1060942856365727e-07
3.3564646173545043e-07
3.147937377434573e-07
1.8065838958136737e-07
3.9650745975450263e-07
2.5411523552065773e-07
3.4018324868156924e-07
2.3468606968890526e-07
4.186587432286615e-07
3.7411672337839263e-07
2.4968474576780864e-07
4.461306843950297e-07
3.3532407428538136e-07
2.769883167275111e-07
4.14689679928415e-07
3.808480073530518e-07
3.2440837571812153e-07
2.6192412860837067e-07
2.6441247769071197e-07
6.899596769471827e-07
5.267544906928379e-07
8.222922360801022e-07
4.4250717223803804e-07
8.87740327470965e-07
2.1764029156656

Episodes:  22%|██▏       | 648/3000 [21:54:36<115:32:46, 176.86s/it]

2.3385584313473373e-07
2.4901976303226547e-07
2.4546477561671054e-07
3.484096566808148e-07
2.663486782239488e-07
3.130129186956765e-07
3.0599562705901917e-07
5.514232839232136e-07
3.8938486568440567e-07
7.760930316180747e-07


In [22]:
#============ Duration per Episode =====================

# figure_title = 'DQN with position as auxiliary reward' # = filename
# plot_durations(figure_title, savefig=False, show_result=True)

In [9]:
print(agent.episode_durations)

NameError: name 'agent' is not defined

In [10]:
#============ Episode Durations, Scatterplot =====================

# plot_scatter(episode_durations, 'Episode', 'Duration')
# plt.show()

In [ ]:
#============ Loss Curve =====================

plot_curve(agent.loss_per_episode, 'Loss Curve', 'Training Step', 'Loss')
plt.show()

# report loss
print("final loss:", loss_per_episode[-1])

# report average cumulative reward per ep
average_cumulative_reward_per_episode = np.mean(cumulative_reward_per_episode)
print('average_cumulative_reward_per_episode = ', average_cumulative_reward_per_episode)


In [ ]:
#============ Cumulative Reward per Episode =====================

#plot_with_average(cumulative_reward_per_episode, 'Episode', 'Cumulative Reward')

In [ ]:
#============ Cumulative Reward per Episode, Scatterplot =====================

# plot_scatter(cumulative_reward_per_episode, 'Episode', 'Cumulative Reward')
# plt.show()

In [ ]:
#============ Composition of Averaged Cumulative Reward per Episode =====================

data_t = torch.tensor(cumulative_reward_per_episode, dtype=torch.float)
plt.title('Composition of Averaged Cumulative Reward per Episode')
plt.xlabel('Episode')
plt.ylabel('Cumulative Reward')
c_e_r_p_e_t = torch.tensor(cumulative_environment_reward_per_episode, dtype=torch.float)
c_a_r_p_e_t = torch.tensor(cumulative_auxiliary_reward_per_episode, dtype=torch.float)
if len(c_e_r_p_e_t) > 100:  # Check if data has more than 100 episodes
        means = data_t[100:].unfold(0, 100, 1).mean(1).view(-1)
        # Plot the average line starting from episode 100
        plt.plot(range(100, len(cumulative_reward_per_episode)-99), means.numpy(), label='Cumulative Reward Per Episode')
        # Calculate moving average starting from episode 100
        means = c_e_r_p_e_t[100:].unfold(0, 100, 1).mean(1).view(-1)
        # Plot the average line starting from episode 100
        plt.plot(range(100, len(cumulative_environment_reward_per_episode)-99), means.numpy(), label='Cumulative Environment Reward Per Episode')
        means = c_a_r_p_e_t[100:].unfold(0, 100, 1).mean(1).view(-1)
        # Plot the average line starting from episode 100
        plt.plot(range(100, len(cumulative_auxiliary_reward_per_episode)-99), means.numpy(), label='Cumulative Auxiliary Reward Per Episode')

plt.legend()
plt.show()

In [ ]:
# #============ Cumulative number of successes per Episode =====================

# cumulative_reward = cumulative_sum(cumulative_reward_per_episode)
# cumulative_environment_reward = cumulative_sum(cumulative_environment_reward_per_episode)
# cumulative_auxiliary_reward = cumulative_sum(cumulative_auxiliary_reward_per_episode)

# #separately depict the environment reward, the auxiliary reward and their sum
# #### SMOOTHEN IF NECESSARY
# plt.figure(1)
# plt.title('Composition of Cumulative Reward')
# plt.xlabel('Episode')
# plt.ylabel('Cumulative Reward')
# plt.plot(cumulative_reward, label='Cumulative Reward')
# plt.plot(cumulative_environment_reward, label='Environment Reward')
# plt.plot(cumulative_auxiliary_reward, label='Auxiliary Reward')

# plt.legend()  # Show legend

In [ ]:
#============ Cumulative number of successes =====================

cumulative_successes = cumulative_sum(agent_performance)
plot_curve(cumulative_successes, 'Cumulative Number of Successes', 'Episodes', 'Successes', savefig=False)